In [1]:
import os
import numpy as np

if not os.path.basename(os.getcwd()) == "ThousandSuns":
    os.chdir("..")  # Run Once!
%load_ext autoreload
%autoreload 2

from output_graphs.hourly_graph_creator import *
from df_objects.df_objects import ElectricityUseDf, DemandDf, ProductionDf, CostElectricityDf
from hourly_simulation.parameters import simulation_params, Params
from hourly_simulation.predict_demand import predict_demand_in_year
from hourly_simulation.strategies import selling_strategy
from hourly_simulation.parameters import simulation_params
from tests.sanity_checks import test_simulation
import logging

logging.getLogger().setLevel(logging.INFO)

In [ ]:
num_batteries = 1
print("*Under production*")
future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [9] * 24}))
price: CostElectricityDf = CostElectricityDf(pd.DataFrame({"Cost ILS/Kwh": [100 for i in range(80, 104)],
                                                           "HourOfYear": [i for i in range(80, 104)]}))
binary_price: CostElectricityDf = CostElectricityDf(pd.DataFrame({"Cost ILS/Kwh": [0 for i in range(80, 104)],
                                                           "HourOfYear": [i for i in range(80, 104)]}))

simulation_params_dict = simulation_params._asdict()
simulation_params_dict['MAX_SELLING_POWER'] = 1
simulation_params_dict['CHARGE_POWER'] = 1
simulation_params_dict['BATTERY_CAPACITY'] = 2
simulation_params = Params(**simulation_params_dict)
electricity_use: ElectricityUseDf = selling_strategy.first_selling_strategy(
    demand=future_demand, production=total_panel_production, param= simulation_params, number_of_batteries=num_batteries)
daily_graph(electricity_use.df)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                params=simulation_params, num_batteries=num_batteries)

In [ ]:
print("*Over production*")
future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10.0] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [11.0] * 24}))
electricity_use: ElectricityUseDf = selling_strategy.first_selling_strategy(
    demand=future_demand, production=total_panel_production, param= simulation_params, number_of_batteries=num_batteries)
daily_graph(electricity_use.df)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                params=simulation_params, num_batteries=num_batteries)

In [ ]:
print("*Oscillations around demand*")
future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [10 + 2 * np.sin(2 * np.pi * x / 6)
                                                                                      for x in range(24)]}))
electricity_use: ElectricityUseDf = selling_strategy.first_selling_strategy(
    demand=future_demand, production=total_panel_production, param= simulation_params, number_of_batteries=num_batteries)
daily_graph(electricity_use.df)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                params=simulation_params, num_batteries=num_batteries)

In [ ]:
num_batteries = 1
print("*Under production*")
binary_cost_list = [0] * 17 + [1] * 7
cost_list = [10] * 17 + [20] * 7

future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [9] * 24}))
price: CostElectricityDf = CostElectricityDf(pd.DataFrame({"Cost ILS/Kwh": cost_list,
                                                           "HourOfYear": [i for i in range(80, 104)]}))
binary_price: CostElectricityDf = CostElectricityDf(pd.DataFrame({"Cost ILS/Kwh": binary_cost_list,
                                                           "HourOfYear": [i for i in range(80, 104)]}))

# electricity_use: ElectricityUseDf = strategies.first_selling_strategy(
#     demand=future_demand, production=total_panel_production,
#     battery_capacity=num_batteries * simulation_params.BATTERY_CAPACITY,
#     battery_power=num_batteries * simulation_params.CHARGE_POWER, battery_efficiency=0.87, cost_profile=price, binary_cost_profile=binary_price, sell_profile=price, sale_max_power=0.1)

simulation_params_dict = simulation_params._asdict()
simulation_params_dict['MAX_SELLING_POWER'] = 10
simulation_params_dict['CHARGE_POWER'] = 4
simulation_params_dict['BATTERY_CAPACITY'] = 2
simulation_params = Params(**simulation_params_dict)
print("*Oscillating production")
future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [10 + 2 * np.sin(2 * np.pi * x / 6)
                                                                                      for x in range(24)]}))
electricity_use: ElectricityUseDf = selling_strategy.first_selling_strategy(
    demand=future_demand, production=total_panel_production, param= simulation_params, number_of_batteries=num_batteries)
daily_graph(electricity_use.df)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                params=simulation_params, num_batteries=num_batteries)

In [32]:
from hourly_simulation.shift_day_in_year import shift_day_of_year
num_batteries = 10
solar_panel_power_kw = 5473
demand = DemandDf(pd.read_csv(r'data/simulation_demand_input/consumption_hatzor.csv', index_col=0))
future_demand, data_year = predict_demand_in_year(demand, params=simulation_params, simulated_year=2020)
normalised_production = ProductionDf(
    pd.read_csv("data/simulation_production_profile/national_solar_production.csv", index_col=0))
normalised_production.df[normalised_production.SolarProduction] /= normalised_production.df[
    normalised_production.SolarProduction].max()
total_panel_production = ProductionDf(normalised_production.df.copy())
total_panel_production.df[total_panel_production.SolarProduction] *= solar_panel_power_kw
# selling_cost = CostElectricityDf(pd.read_csv(r'data/electricity_cost2.csv', index_col=0))
# selling_cost.df[selling_cost.Cost] *= 0
binary_cost = CostElectricityDf(pd.read_csv(r'data/electricity_cost_binary.csv', index_col=0))
simulation_params_dict = simulation_params._asdict()
simulation_params_dict['MAX_SELLING_POWER'] = 14000
simulation_params_dict['CHARGE_POWER'] = 2000
simulation_params_dict['BATTERY_CAPACITY'] = 4000
simulation_params = Params(**simulation_params_dict)
electricity_use: ElectricityUseDf = selling_strategy.first_selling_strategy(
    demand=future_demand, production=total_panel_production, param= simulation_params, number_of_batteries=num_batteries, predict_demand_in_year=data_year)
yearly_graph(electricity_use.df, batteries_num=num_batteries, batteries_cap=num_batteries * simulation_params.BATTERY_CAPACITY, demand=demand)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                params=simulation_params, num_batteries=num_batteries)

day 63
[0. 0. 0. ... 0. 0. 0.]


INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:passed test_charge_power_not_passed
INFO:root:passed test_selling_limit_not_passed
INFO:root:Passed all tests


In [23]:
electricity_use.df

GasUsage  SolarUsage  StoredUsage  SolarStored  SolarLost  SolarSold  \
0       1236.0         0.0          0.0          0.0        0.0        0.0   
1       1215.0         0.0          0.0          0.0        0.0        0.0   
2       1180.0         0.0          0.0          0.0        0.0        0.0   
3       1145.0         0.0          0.0          0.0        0.0        0.0   
4       1145.0         0.0          0.0          0.0        0.0        0.0   
...        ...         ...          ...          ...        ...        ...   
8755       0.0         0.0       1524.0          0.0        0.0        0.0   
8756       0.0         0.0       1480.0          0.0        0.0        0.0   
8757       0.0         0.0       1375.0          0.0        0.0        0.0   
8758    1243.0         0.0          0.0          0.0        0.0        0.0   
8759    1178.0         0.0          0.0          0.0        0.0        0.0   

      StoredSold  GasStored  HourOfYear  
0        0.00000        0.0           1  
1        0.00000        0.0           2  
2        0.00000        0.0           3  
3        0.00000        0.0           4  
4        0.00000        0.0           5  
...          ...        ...         ...  
8755  3758.95339        0.0        8756  
8756     0.00000        0.0        8757  
8757     0.00000        0.0        8758  
8758     0.00000        0.0        8759  
8759     0.00000        0.0        8760  

[8760 rows x 9 columns]

In [11]:
electricity_use